# Ingesting realtime tweets 

In [42]:
import tweepy
import time
from kafka import KafkaConsumer, KafkaProducer
import csv

### Twitter setup

In [43]:
# twitter setup
consumer_key = "3cSaGgMXZGNtHw2nGMzS67oZ0"
consumer_secret = "uK2Ny7rD0RYmjku54LVpRjxG6EPMGYKmzkHAze1XT1OgpDHDEf"
access_token = "933397205985218570-stOqCQwrfaj66WdxKZxWaPtu7SVjPqJ"
access_token_secret = "STPtNp6QhwGylbuFYd73UXQ7FT6GYSWYcr6GdUMHJnBQ8"
# Auth
auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token, access_token_secret)
api = tweepy.API(auth,wait_on_rate_limit=True) 

# redshift

In [43]:
import psycopg2

In [44]:
config = { 'dbname': 'dev', 
           'user':'root',
           'pwd':'PublicoRoot1',
           'host':'datampcluster.c7onviryvrw8.us-east-2.redshift.amazonaws.com',
           'port':'5439'
         }

In [45]:
conn =  psycopg2.connect(dbname=config['dbname'], host=config['host'], 
                              port=config['port'], user=config['user'], 
                              password=config['pwd'])

normalize the time

In [5]:
from datetime import datetime, timedelta

def normalize_timestamp(time):
    mytime = datetime.strptime(time, "%Y-%m-%d %H:%M:%S")
    mytime += timedelta(hours=1)   # the tweets are timestamped in GMT timezone, while I am in +1 timezone
    return (mytime.strftime("%Y-%m-%d %H:%M:%S")) 

### Kafka producer

In [47]:
producer = KafkaProducer(bootstrap_servers='localhost:9092')
topic_name = 'DM'


    - id 
    - created_at
    - followers_count
    - location
    - favorite_count
    - retweet_count

In [48]:
def compute_get_twit_count(conn, get_count,twit_count):
    curs = conn.cursor()
    curs.execute(""" 
        insert into twit_count(counts)
        select """+str(twit_count)+""";
        insert into get_twit_count(counts)
        select """+str(get_count)+""";
    """)
    curs.close()
    conn.commit()


In [6]:
def get_twitter_data():
    res = api.search("#happy",rpp = 100,count=1000)
    twit_count = 0
    for i in res:
        twit_count += 1
        record = ''
        record += str(i.user.id_str)
        record += ';'
        record += str(normalize_timestamp(str(i.created_at)))
        record += ';'
        record += str(i.user.followers_count)
        record += ';'
        record += str(i.user.location)
        record += ';'
        record += str(i.favorite_count)
        record += ';'
        record += str(i.retweet_count)
        record += ';'
        producer.send(topic_name, str.encode(record))
    return twit_count

In [30]:
get_count = 0
twit_count = 0
count = 0
last_id = -1
count += 1
get_count += 1
aux_twit_count , last_id = get_twitter_data(last_id)
print (str(last_id)+" ; "+str(aux_twit_count))
twit_count += aux_twit_count
time.sleep(interval)

100
24
19
6
12
4
0
not founded
1045250906021941248 ; 165


NameError: name 'interval' is not defined

In [44]:
searched_tweets = []
def get_twitter_data(last_id = -1):
    query = "#Corrupcion"
    max_tweets = 1000
    searched_tweets = []
    csvFile = open('ua.csv', 'a')
    #Use csv Writer
    csvWriter = csv.writer(csvFile)
    while len(searched_tweets) < max_tweets:
        count = max_tweets - len(searched_tweets)
        print(str(last_id))
        try:
#             new_tweets2 = tweepy.Cursor(api.search,q=query,count=count,
#                             lang = "es",
#                             since="2019-06-03",
#                             since_id=str(last_id)).items()
            new_tweets = api.search(q=query, count=count, since="2019-06-03", since_id=str(last_id), lang = "es")
            print (len(new_tweets))
            if not new_tweets:
                print ("not founded")
                break
            searched_tweets.extend(new_tweets)
            last_id = new_tweets[0].id
        except tweepy.TweepError as e:
            # depending on TweepError.code, one may want to retry or wait
            # to keep things simple, we will give up on an error
            print (e)
            break
#         print ("first,"+new_tweets)
#         print (new_tweets2)
    twit_count = 0
    for tweet in searched_tweets:
        csvWriter.writerow([tweet.created_at, tweet.text.encode('utf-8')])
        twit_count += 1
#         record = ''
#         record += str(i.user.id_str)
#         record += ';'
#         record += str(normalize_timestamp(str(i.created_at)))
#         record += ';'
#         record += str(i.user.followers_count)
#         record += ';'
#         record += str(i.user.location)
#         record += ';'
#         record += str(i.favorite_count)
#         record += ';'
#         record += str(i.retweet_count)
#         record += ';'
        #producer.send(topic_name, str.encode(record))
    return twit_count, last_id #searched_tweets#

In [75]:
###############################3 with cursor


searched_tweets = []
def get_twitter_data(last_id = -1):
    query = "#Corrupcion"
    max_tweets = 1000
    searched_tweets = []
    csvFile = open('ua.csv', 'a')
    #Use csv Writer
    csvWriter = csv.writer(csvFile)
#     while True:#len(searched_tweets) < max_tweets:
        #count = max_tweets - len(searched_tweets)
    print(str(last_id))
    try:
        new_tweets = tweepy.Cursor(api.search,q=query,count=max_tweets,
                        lang = "es",
                        since="2019-06-03").items()
        if not new_tweets:
            print ("not founded")
        searched_tweets = new_tweets
        print("finished", new_tweets)#searched_tweets)
    except tweepy.TweepError as e:
        # depending on TweepError.code, one may want to retry or wait
        # to keep things simple, we will give up on an error
        print (e)
    twit_count = 0
    #print(searched_tweets.count())
    for tweet in searched_tweets:
        print (tweet)
        csvWriter.writerow([tweet.created_at, tweet.text.encode('utf-8')])
        twit_count += 1
#         record = ''
#         record += str(i.user.id_str)
#         record += ';'
#         record += str(normalize_timestamp(str(i.created_at)))
#         record += ';'
#         record += str(i.user.followers_count)
#         record += ';'
#         record += str(i.user.location)
#         record += ';'
#         record += str(i.favorite_count)
#         record += ';'
#         record += str(i.retweet_count)
#         record += ';'
        #producer.send(topic_name, str.encode(record))
    csvFile.close()

In [76]:
get_twitter_data(-1)
sd

-1
finished <tweepy.cursor.ItemIterator object at 0x00000267E5D2FF60>
Status(_api=<tweepy.api.API object at 0x00000267E563FEB8>, _json={'created_at': 'Tue Jun 04 15:04:16 +0000 2019', 'id': 1135925239026716673, 'id_str': '1135925239026716673', 'text': "RT @SoyArepita: *Cleptocracia\xa0(del\xa0griego\xa0clepto, 'robo'; y\xa0cracia, 'poder' = dominio de los ladrones) es el establecimiento y desarrollo d…", 'truncated': False, 'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [{'screen_name': 'SoyArepita', 'name': 'Arepita', 'id': 843841119335124992, 'id_str': '843841119335124992', 'indices': [3, 14]}], 'urls': []}, 'metadata': {'iso_language_code': 'es', 'result_type': 'recent'}, 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 130379871, 'id_str': '13037987

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Status(_api=<tweepy.api.API object at 0x00000267E563FEB8>, _json={'created_at': 'Tue Jun 04 04:02:09 +0000 2019', 'id': 1135758614239612930, 'id_str': '1135758614239612930', 'text': 'RT @cnahonduras: #Corrupcion | Los tentáculos de la corrupción denunciados por el CNA, le han quitado la posibilidad de poseer infraestruct…', 'truncated': False, 'entities': {'hashtags': [{'text': 'Corrupcion', 'indices': [17, 28]}], 'symbols': [], 'user_mentions': [{'screen_name': 'cnahonduras', 'name': 'CNA Honduras', 'id': 757973101518942208, 'id_str': '757973101518942208', 'indices': [3, 15]}], 'urls': []}, 'metadata': {'iso_language_code': 'es', 'result_type': 'recent'}, 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1147019059, 'id_str': '1147019059', 'name': 'Carlos Javier Ir

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Status(_api=<tweepy.api.API object at 0x00000267E563FEB8>, _json={'created_at': 'Mon Jun 03 18:20:37 +0000 2019', 'id': 1135612267091890176, 'id_str': '1135612267091890176', 'text': 'En contraste, en #Ecuador el gobierno neoliberal de #LenínMoreno desmerece las escuelas del milenio y reabre las mi… https://t.co/MhZXKdipqM', 'truncated': True, 'entities': {'hashtags': [{'text': 'Ecuador', 'indices': [17, 25]}, {'text': 'LenínMoreno', 'indices': [52, 64]}], 'symbols': [], 'user_mentions': [], 'urls': [{'url': 'https://t.co/MhZXKdipqM', 'expanded_url': 'https://twitter.com/i/web/status/1135612267091890176', 'display_url': 'twitter.com/i/web/status/1…', 'indices': [117, 140]}]}, 'metadata': {'iso_language_code': 'es', 'result_type': 'recent'}, 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Status(_api=<tweepy.api.API object at 0x00000267E563FEB8>, _json={'created_at': 'Mon Jun 03 06:00:15 +0000 2019', 'id': 1135425945635098624, 'id_str': '1135425945635098624', 'text': 'RT @PedroElBasque: Ya se la pelearon #Prianistas, Barbosa se irá contra todo lo relacionado con la #Corrupción #BarbosaGobernador https://t…', 'truncated': False, 'entities': {'hashtags': [{'text': 'Prianistas', 'indices': [37, 48]}, {'text': 'Corrupción', 'indices': [99, 110]}, {'text': 'BarbosaGobernador', 'indices': [111, 129]}], 'symbols': [], 'user_mentions': [{'screen_name': 'PedroElBasque', 'name': 'Pedrito', 'id': 803765636992221189, 'id_str': '803765636992221189', 'indices': [3, 17]}], 'urls': []}, 'metadata': {'iso_language_code': 'es', 'result_type': 'recent'}, 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_s

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Status(_api=<tweepy.api.API object at 0x00000267E563FEB8>, _json={'created_at': 'Mon Jun 03 00:09:56 +0000 2019', 'id': 1135337786112913414, 'id_str': '1135337786112913414', 'text': 'RT @LulydelMar: #MacriMegaCorrupto \nQue Macri es el campeón de la #Corrupcion lo sabe todo el mundo hace rato \n#HaganAlgo https://t.co/zrHy…', 'truncated': False, 'entities': {'hashtags': [{'text': 'MacriMegaCorrupto', 'indices': [16, 34]}, {'text': 'Corrupcion', 'indices': [66, 77]}, {'text': 'HaganAlgo', 'indices': [111, 121]}], 'symbols': [], 'user_mentions': [{'screen_name': 'LulydelMar', 'name': 'LoLa ✌️', 'id': 2959738865, 'id_str': '2959738865', 'indices': [3, 14]}], 'urls': []}, 'metadata': {'iso_language_code': 'es', 'result_type': 'recent'}, 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'i

NameError: name 'sd' is not defined

In [16]:
searched_tweets

[]

### Deployment 

In [51]:
def periodic_work(interval):
    get_count = 0
    twit_count = 0
    count = 0
    last_id = -1
    while True:
        count += 1
        get_count += 1
        aux_twit_count , last_id = get_twitter_data(last_id)
        print (str(last_id)+" ; "+str(aux_twit_count))
        twit_count += aux_twit_count
        if count == 20:
            compute_get_twit_count(conn, get_count, twit_count)
            twit_count = 0
        #interval should be an integer, the number of seconds to wait
        time.sleep(interval)


In [ ]:
periodic_work(60)  # get data every couple of minutes

100
46
15
18
22
28
22
28
25
22
18
21
12
11
8
9
12
11
11
17
15
18
16
13
16
27
24
9
15
16
7
40
25
16
28
25
21
16
24
24
20
10
7
5
5
11
20
25
11
24
11
1045291037105754112 ; 1000
100
40
17
11
33
24
19
16
11
16
10
16
18
17
12
20
14
17
31
23
11
8
15
16
18
17
27
24
17
25
8
19
35
37
26
26
15
14
25
11
16
11
14
15
22
15
13
27
8
1045291532876746753 ; 1000
100
47
19
10
21
32
27
16
11
18
17
21
20
16
17
16
16
17
24
30
27
22
30
24
26
23
15
10
11
16
11
28
24
26
32
16
21
22
19
26
